<h1 align=center><font size = 5>Find the wifi locations in new york</font></h1>

## Part 1: description of the problem and a discussion of the background

The world is large and also small, because now everyone is connected with each other through internet. We can send messages, have vedio calls, share happy moments through the internet to the people around the world, wherever we are. Is this true? Yes, but we have to have the access to the internet everywhere. The mobile provider companies offer a lot of data plans, for some people, these data plans are not enough especially during the travel and much higher data amount is required. Therefore, looking for wifi locations is important.
In this project, we will map the wifi locations in new york, which could be used for people to find where they can get the wifi in new york.

## Part 2: description of the data

The data is downloaded from the NYC open data website https://data.cityofnewyork.us/Social-Services/NYC-Wi-Fi-Hotspot-Locations/a9we-mtpn.

Import the required library

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    openssl-1.0.2p             |       h470a237_1         3.1 MB  conda-forge
    geopy-1.17.0               |             py_0          49 KB  conda-forge
    certifi-2018.11.29         |        py36_1000         145 KB  conda-forge
    conda-4.5.11               |        py36_1000         651 KB  conda-forge
    ca-certificates-2018.11.29 |       ha4d7672_0         143 KB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         4.1 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.49-py_0            conda-forge
    geopy:           

In [34]:
df_wifi = pd.read_csv('NYC_Free_Public_WiFi_03292017.csv')

print('Dataset downloaded and read into a pandas dataframe!')

Dataset downloaded and read into a pandas dataframe!


In [35]:
df_wifi.head()

BORO                                       the_geom  TYPE  OBJECTID  \
0   QU  POINT (-73.94458300007643 40.755726999970044)  Free      8641   
1   QU  POINT (-73.94413100020707 40.755332999617764)  Free      8642   
2   QU   POINT (-73.94516599972107 40.75575100007361)  Free      8643   
3   QU   POINT (-73.94516599972107 40.75575100007361)  Free      8644   
4   QU   POINT (-73.94516599972107 40.75575100007361)  Free      8645   

           PROVIDER                                            NAME  \
0  Spot On Networks  QUEENS BRIDGE - JACOB A. RIIS Settlement House   
1  Spot On Networks  QUEENS BRIDGE - JACOB A. RIIS Settlement House   
2  Spot On Networks  QUEENS BRIDGE - JACOB A. RIIS Settlement House   
3  Spot On Networks  QUEENS BRIDGE - JACOB A. RIIS Settlement House   
4  Spot On Networks  QUEENS BRIDGE - JACOB A. RIIS Settlement House   

         LAT         LOCATION        LON              X              Y  \
0  40.755727  10-25 41 AVENUE -73.944583  999603.226171  214613.274563   
1  40.755333  10-43 41 AVENUE -73.944131  999728.543834  214469.807003   
2  40.755751  10-05 41 AVENUE -73.945166  999441.701232  214621.916935   
3  40.755751  10-05 41 AVENUE -73.945166  999441.701232  214621.916935   
4  40.755751  10-05 41 AVENUE -73.945166  999441.701232  214621.916935   

                                   LOCATION_T  \
0  Indoor AP - Community Center - Computer Rm   
1           Indoor AP - Queens Public Library   
2         Indoor AP - North Management Office   
3         Indoor AP - North Management Office   
4          Indoor AP - North Maintenance Area   

                             REMARKS    CITY                   SSID  \
0  Free - Up to 25 mbs Wi-Fi Service  Queens  Quensbridge Connected   
1  Free - Up to 25 mbs Wi-Fi Service  Queens  Quensbridge Connected   
2  Free - Up to 25 mbs Wi-Fi Service  Queens  Quensbridge Connected   
3  Free - Up to 25 mbs Wi-Fi Service  Queens  Quensbridge Connected   
4  Free - Up to 25 mbs Wi-Fi Service  Queens  Quensbridge Connected   

                SOURCEID                     ACTIVATED  BOROCODE BORONAME  \
0  NYC HOUSING AUTHORITY  05/01/2018 12:00:00 AM +0000         4   Queens   
1  NYC HOUSING AUTHORITY  05/01/2018 12:00:00 AM +0000         4   Queens   
2  NYC HOUSING AUTHORITY  05/01/2018 12:00:00 AM +0000         4   Queens   
3  NYC HOUSING AUTHORITY  05/01/2018 12:00:00 AM +0000         4   Queens   
4  NYC HOUSING AUTHORITY  05/01/2018 12:00:00 AM +0000         4   Queens   

  NTACODE                                   NTANAME  COUNDIST  POSTCODE  \
0    QN68  Queensbridge-Ravenswood-Long Island City        26     11101   
1    QN68  Queensbridge-Ravenswood-Long Island City        26     11101   
2    QN68  Queensbridge-Ravenswood-Long Island City        26     11101   
3    QN68  Queensbridge-Ravenswood-Long Island City        26     11101   
4    QN68  Queensbridge-Ravenswood-Long Island City        26     11101   

   BOROCD  CT2010  BOROCT2010      BIN         BBL  DOITT_ID  
0     401      25     4002500  4433386  4004700100      4746  
1     401      25     4002500  4433386  4004700100      4747  
2     401      25     4002500  4433386  4004700100      4748  
3     401      25     4002500  4433386  4004700100      4749  
4     401      25     4002500  4433386  4004700100      4750

In [36]:
# print the dimensions of the dataframe
print(df_wifi.shape)

(3345, 29)


## Part 3: clean the data

In [37]:
df_wifi.drop(['BORO', 'the_geom', 'TYPE', 'OBJECTID', 'PROVIDER', 'LOCATION', 'X', 'Y', 'LOCATION_T', 'REMARKS', 'SSID', 'SOURCEID', 'ACTIVATED', 'BOROCODE', 'BORONAME', 'NTACODE', 'NTANAME', 'COUNDIST', 'POSTCODE', 'BOROCD', 'CT2010','BOROCT2010', 'BIN', 'BBL', 'DOITT_ID'], axis=1, inplace=True)

# let's view the first five elements and see how the dataframe was changed
df_wifi.head()

NAME        LAT        LON  \
0  QUEENS BRIDGE - JACOB A. RIIS Settlement House  40.755727 -73.944583   
1  QUEENS BRIDGE - JACOB A. RIIS Settlement House  40.755333 -73.944131   
2  QUEENS BRIDGE - JACOB A. RIIS Settlement House  40.755751 -73.945166   
3  QUEENS BRIDGE - JACOB A. RIIS Settlement House  40.755751 -73.945166   
4  QUEENS BRIDGE - JACOB A. RIIS Settlement House  40.755751 -73.945166   

     CITY  
0  Queens  
1  Queens  
2  Queens  
3  Queens  
4  Queens

In [40]:
df_wifi.rename(columns={'LAT':'Latitude', 'LON':'Longitude','CITY':'Borough'}, inplace=True)

# let's view the first five elements and see how the dataframe was changed
df_wifi.head()

NAME   Latitude  Longitude  \
0  QUEENS BRIDGE - JACOB A. RIIS Settlement House  40.755727 -73.944583   
1  QUEENS BRIDGE - JACOB A. RIIS Settlement House  40.755333 -73.944131   
2  QUEENS BRIDGE - JACOB A. RIIS Settlement House  40.755751 -73.945166   
3  QUEENS BRIDGE - JACOB A. RIIS Settlement House  40.755751 -73.945166   
4  QUEENS BRIDGE - JACOB A. RIIS Settlement House  40.755751 -73.945166   

  Borough  
0  Queens  
1  Queens  
2  Queens  
3  Queens  
4  Queens

In [41]:
df_wifi.shape

(3345, 4)

## Part 4: map the data

In [30]:
address = 'New York City, NY'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

/home/jupyterlab/conda/lib/python3.6/site-packages/geopy/geocoders/osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


The geograpical coordinate of New York City are 40.7308619, -73.9871558.


In [42]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)
   
map_newyork

In [46]:
# add markers to map
for lat, lng, borough, name in zip(df_wifi['Latitude'], df_wifi['Longitude'], df_wifi['Borough'], df_wifi['NAME']):
    label = '{}, {}'.format(name, city)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)

map_newyork

## Part 5: use foursquare API

In [47]:
CLIENT_ID = 'J20AXLHIJXZSFG1NAFSPOM21NHVQYY42MVMMFEZLA24JLEZ3' # your Foursquare ID
CLIENT_SECRET = 'CEYOY5FOPEFZQEBWVEIQQKCVZSAVMBIQTXNYZI5C3MDIAIQC' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: J20AXLHIJXZSFG1NAFSPOM21NHVQYY42MVMMFEZLA24JLEZ3
CLIENT_SECRET:CEYOY5FOPEFZQEBWVEIQQKCVZSAVMBIQTXNYZI5C3MDIAIQC


In [49]:
# Get the index100 name
df_wifi.loc[100, 'NAME']

'Prospect Park'

In [52]:
name_latitude = df_wifi.loc[100, 'Latitude'] # name latitude value
name_longitude = df_wifi.loc[100, 'Longitude'] # name longitude value

name = df_wifi.loc[100, 'NAME'] # name of the wifi

print('Latitude and longitude values of {} are {}, {}.'.format(name, 
                                                               name_latitude, 
                                                               name_longitude))

Latitude and longitude values of Prospect Park are 40.657001, -73.963697.


In [53]:
LIMIT = 50 # limit of number of venues returned by Foursquare API

radius = 500 # define radius

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    name_latitude, 
    name_longitude, 
    radius, 
    LIMIT)
url # display URL


'https://api.foursquare.com/v2/venues/explore?&client_id=J20AXLHIJXZSFG1NAFSPOM21NHVQYY42MVMMFEZLA24JLEZ3&client_secret=CEYOY5FOPEFZQEBWVEIQQKCVZSAVMBIQTXNYZI5C3MDIAIQC&v=20180605&ll=40.657001,-73.963697&radius=500&limit=50'

In [54]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5c05f140f594df18fb7c7d63'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': '$-$$$$', 'key': 'price'},
    {'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Prospect Park',
  'headerFullLocation': 'Prospect Park, Brooklyn',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 45,
  'suggestedBounds': {'ne': {'lat': 40.6615010045, 'lng': -73.95777627325832},
   'sw': {'lat': 40.6525009955, 'lng': -73.96961772674167}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '5267c3e1498ef981529b551d',
       'name': 'LeFrak Center at Lakeside',
       'location': {'address': '171 East Drive',
        'crossStreet': 'Parkside Ave',
        'lat': 40.656993881673024,
        'lng': -73.

In [55]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [56]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON



nearby_venues.head()

reasons.count                                      reasons.items  \
0              0  [{'summary': 'This spot is popular', 'type': '...   
1              0  [{'summary': 'This spot is popular', 'type': '...   
2              0  [{'summary': 'This spot is popular', 'type': '...   
3              0  [{'summary': 'This spot is popular', 'type': '...   
4              0  [{'summary': 'This spot is popular', 'type': '...   

                       referralId  \
0  e-0-5267c3e1498ef981529b551d-0   
1  e-0-4edbdcdf9a5286d9211cacd6-1   
2  e-0-583726ea424f93797198514e-2   
3  e-0-4bddff7ee75c0f47cd7bc603-3   
4  e-0-5320b02a498e847d9e93b82b-4   

                                    venue.categories venue.delivery.id  \
0  [{'id': '4bf58dd8d48988d168941735', 'name': 'S...               NaN   
1  [{'id': '4bf58dd8d48988d163941735', 'name': 'P...               NaN   
2  [{'id': '4bf58dd8d48988d114951735', 'name': 'B...               NaN   
3  [{'id': '4bf58dd8d48988d1e5931735', 'name': 'M...               NaN   
4  [{'id': '4bf58dd8d48988d16d941735', 'name': 'C...            374524   

          venue.delivery.provider.icon.name  \
0                                       NaN   
1                                       NaN   
2                                       NaN   
3                                       NaN   
4  /delivery_provider_seamless_20180129.png   

        venue.delivery.provider.icon.prefix  \
0                                       NaN   
1                                       NaN   
2                                       NaN   
3                                       NaN   
4  https://fastly.4sqi.net/img/general/cap/   

  venue.delivery.provider.icon.sizes venue.delivery.provider.name  \
0                                NaN                          NaN   
1                                NaN                          NaN   
2                                NaN                          NaN   
3                                NaN                          NaN   
4                           [40, 50]                     seamless   

                                  venue.delivery.url  \
0                                                NaN   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4  https://www.seamless.com/menu/blessings-cafe-6...   

                   venue.id venue.location.address venue.location.cc  \
0  5267c3e1498ef981529b551d         171 East Drive                US   
1  4edbdcdf9a5286d9211cacd6                    NaN                US   
2  583726ea424f93797198514e       632 Flatbush Ave                US   
3  4bddff7ee75c0f47cd7bc603          Prospect Park                US   
4  5320b02a498e847d9e93b82b       663 Flatbush Ave                US   

  venue.location.city venue.location.country venue.location.crossStreet  \
0            Brooklyn          United States               Parkside Ave   
1            Brooklyn          United States                        NaN   
2            Brooklyn          United States                Fenimore St   
3            Brooklyn          United States                        NaN   
4            Brooklyn          United States                  Hawthorne   

   venue.location.distance                    venue.location.formattedAddress  \
0                       18  [171 East Drive (Parkside Ave), Brooklyn, NY 1...   
1                      251                [Brooklyn, NY 11226, United States]   
2                      285  [632 Flatbush Ave (Fenimore St), Brooklyn, NY ...   
3                      134  [Prospect Park, Brooklyn, NY 11225, United Sta...   
4                      300  [663 Flatbush Ave (Hawthorne), Brooklyn, NY 11...   

                       venue.location.labeledLatLngs  venue.location.lat  \
0  [{'label': 'display', 'lat': 40.65699388167302...           40.656994   
1  [{'label': 'display', 'lat': 40.6550891646217,...           40.6

In [57]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

45 venues were returned by Foursquare.
